In [1]:
import pandas as pd
import pyodbc
from IPython.display import clear_output  # Importa clear_output

# Cargar Excel
df = pd.read_excel(
    r'C:\Users\rrs23\OneDrive\Documentos\OneDrive\Documentos\Datos\BaseQ.xlsx',
    sheet_name='Base Principal'
)

# Limpiar columnas
df.columns = df.columns.str.strip()

# Renombrar columnas clave que usa Servicios
df.rename(columns={
    'Tipo de servicio': 'tipo_de_servicio',
    'Fecha de servicio': 'fecha_de_servicio',
    'Documento del Conductor del Recurso': 'documento_conductor',
    'Conductor': 'nombre_conductor',
    'Correo Cliente': 'correo_cliente',
    'Ciudad': 'ciudad',
    'Descripcion': 'descripcion'
}, inplace=True)

# Limpiar columnas numéricas
for col in ['documento_cliente', 'documento_conductor']:
    df[col] = df[col].astype(str).str.replace(r'[^\d]', '', regex=True)
    df[col] = pd.to_numeric(df[col], errors='coerce').fillna(0).astype(int)

# Formatear fechas correctamente
df['fecha_de_servicio'] = pd.to_datetime(df['fecha_de_servicio'], errors='coerce').fillna(pd.Timestamp('1900-01-01'))

# Rellenar valores nulos para evitar errores al insertar
df['descripcion'] = df['descripcion'].fillna('Sin descripción')
df['tipo_de_servicio'] = df['tipo_de_servicio'].fillna('No especificado')

# Conexión SQL
conn = pyodbc.connect(
    'DRIVER={ODBC Driver 17 for SQL Server};'
    'SERVER=localhost;'
    'DATABASE=quick;'
    'Trusted_Connection=yes;'
)
cursor = conn.cursor()

# Eliminar duplicados para evitar errores de integridad (si aplica)
df_servicios = df.drop_duplicates(subset=[
    'ruta', 'numero_del_servicio', 'documento_cliente', 'documento_conductor', 'codigo_cedi', 'fecha_de_servicio'
])

# Insertar Servicios
servicios_insertados = 0
for i, row in df_servicios.iterrows():
    try:
        cursor.execute("""
            INSERT INTO Servicios (
                ruta, numero_del_servicio, estado, creado_por, documento_cliente,
                documento_conductor, codigo_cedi, fecha_de_servicio, tipo_de_servicio, descripcion
            ) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
        """, row['ruta'], row['numero_del_servicio'], row['estado'], row['creado_por'],
             row['documento_cliente'], row['documento_conductor'], row['codigo_cedi'],
             row['fecha_de_servicio'], row['tipo_de_servicio'], row['descripcion'])

        servicios_insertados += 1

        # Limpiar salida después de cada inserción
        clear_output(wait=True)
        print(f"Servicios insertados: {servicios_insertados}")

    except Exception as e:
        print(f"Error al insertar servicio {row['numero_del_servicio']}: {e}")

conn.commit()





Error al insertar servicio SMI-152035: ('23000', "[23000] [Microsoft][ODBC Driver 17 for SQL Server][SQL Server]Cannot insert the value NULL into column 'id_servicio', table 'quick.dbo.Servicios'; column does not allow nulls. INSERT fails. (515) (SQLExecDirectW); [23000] [Microsoft][ODBC Driver 17 for SQL Server][SQL Server]The statement has been terminated. (3621)")
Error al insertar servicio SMI-158647: ('23000', "[23000] [Microsoft][ODBC Driver 17 for SQL Server][SQL Server]Cannot insert the value NULL into column 'id_servicio', table 'quick.dbo.Servicios'; column does not allow nulls. INSERT fails. (515) (SQLExecDirectW); [23000] [Microsoft][ODBC Driver 17 for SQL Server][SQL Server]The statement has been terminated. (3621)")
Error al insertar servicio SMI-149059: ('23000', "[23000] [Microsoft][ODBC Driver 17 for SQL Server][SQL Server]Cannot insert the value NULL into column 'id_servicio', table 'quick.dbo.Servicios'; column does not allow nulls. INSERT fails. (515) (SQLExecDirect

: 